In [1]:
import pandas as pd
df = pd.read_csv('data/Consumer_Complaints.csv')
df.info()

In [3]:
df.dropna(subset=['Consumer complaint narrative'], inplace=True)

In [6]:
df = df[['Product', 'Sub-product', 'Issue', 'Sub-issue', 'Consumer complaint narrative']]
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 384314 entries, 44142 to 929037
Data columns (total 5 columns):
Product                         384314 non-null object
Sub-product                     332141 non-null object
Issue                           384314 non-null object
Sub-issue                       270512 non-null object
Consumer complaint narrative    384314 non-null object
dtypes: object(5)
memory usage: 17.6+ MB


In [7]:
df.drop_duplicates(inplace=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 368311 entries, 44142 to 929033
Data columns (total 5 columns):
Product                         368311 non-null object
Sub-product                     317919 non-null object
Issue                           368311 non-null object
Sub-issue                       254860 non-null object
Consumer complaint narrative    368311 non-null object
dtypes: object(5)
memory usage: 16.9+ MB


In [72]:
df.head(10)

Product       Sub-product  \
44142  Credit reporting, credit repair services, or o...  Credit reporting   
44206  Credit reporting, credit repair services, or o...  Credit reporting   
44706  Credit reporting, credit repair services, or o...  Credit reporting   
44760  Credit reporting, credit repair services, or o...  Credit reporting   
45420  Credit reporting, credit repair services, or o...  Credit reporting   
45831  Credit reporting, credit repair services, or o...  Credit reporting   
46112  Credit reporting, credit repair services, or o...  Credit reporting   
46228  Credit reporting, credit repair services, or o...  Credit reporting   
46272  Credit reporting, credit repair services, or o...  Credit reporting   
46374  Credit reporting, credit repair services, or o...  Credit reporting   

                                      Issue  \
44142           Improper use of your report   
44206  Incorrect information on your report   
44706  Incorrect information on your report   
44760  Incorrect information on your report   
45420  Incorrect information on your report   
45831  Incorrect information on your report   
46112  Incorrect information on your report   
46228  Incorrect information on your report   
46272  Incorrect information on your report   
46374           Improper use of your report   

                                               Sub-issue  \
44142  Credit inquiries on your report that you don't...   
44206                Information belongs to someone else   
44706                Information belongs to someone else   
44760                Information belongs to someone else   
45420                           Account status incorrect   
45831               Public record information inaccurate   
46112                Information belongs to someone else   
46228                      Account information incorrect   
46272                      Account information incorrect   
46374  Credit inquiries on your report that you don't...   

                            Consumer complaint narrative  
44142  I have reached out to All 3 credit bureaus and...  
44206  I am a victim of identity theft. My personal i...  
44706  I am a victim of identity theft. My personal i...  
44760  On all credit agencies the same accounts are n...  
45420  I have a student loan thats discharge and its ...  
45831  Equifax, XXXX  and XXXX  are all reporting ina...  
46112  This is a writter request to block information...  
46228  The Summer of XX/XX/2018 I was denied a mortga...  
46272  The Summer of XX/XX/XXXXI was denied a mortgag...  
46374  Transunion, XXXX, XXXX all show inquiries to b...

In [97]:
# randomly select num samples
num = 100000
train_data = df[['Consumer complaint narrative']].sample(num, random_state=None)
train_data = train_data['Consumer complaint narrative'].tolist()
print(train_data[0])

XXXX XXXX got a copy of my credit report without permission. I contacted them to inform them they had done this on two separate occasions. They stated they would investigate yet when I got their response letter which I have attached all they did was provide me an unauthorized copy of credit report which they purchased through XXXX. They have NEVER investigated this and each time I have contacted the credit bureaus they have failed to investigate this matter.


In [89]:
import nltk
nltk.download('wordnet')
from nltk.stem.wordnet import WordNetLemmatizer
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
import gensim
from gensim.utils import simple_preprocess
import gensim.corpora as corpora

[nltk_data] Downloading package wordnet to /Users/yunfei/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [26]:
stop_words.extend(['xxxx', 'xx'])
stop_words = set(stop_words)

<class 'set'>


In [61]:
def tokenize(doc):
    # doc is a string
    # return an array of words
    return simple_preprocess(doc, deacc=True, min_len=2, max_len=15)

def rm_stopwords_and_lemmatize(token_array, flag_rm_stop=True, flag_lemmatize=True):
    out = []
    for token in token_array:
        if flag_lemmatize:
            token = WordNetLemmatizer().lemmatize(token)
        if flag_rm_stop:
            if token not in stop_words:
                out.append(token)
        else:
            out.append(token)
    return out

def my_tokenizer(doc, flag_rm_stop=True, flag_lemmatize=True):
    return rm_stopwords_and_lemmatize(tokenize(doc), flag_rm_stop, flag_lemmatize)

In [63]:
text = 'I struggled so much with the settings.'
tokens = tokenize(text)
#print(tokens)
print(rm_stopwords_and_lemmatize(tokens))
#print(rm_stopwords_and_lemmatize(tokens, flag_rm_stop=False))
#print(rm_stopwords_and_lemmatize(tokens, flag_lemmatize=False))
#print(rm_stopwords_and_lemmatize(tokens, flag_rm_stop=False, flag_lemmatize=False))
print(my_tokenizer(text))

['struggled', 'much', 'setting']
['struggled', 'much', 'setting']


In [113]:
print(type(train_data[1]))

<class 'str'>


In [116]:
#define vectorizer parameters
from sklearn.feature_extraction.text import TfidfVectorizer

tfidf_model = TfidfVectorizer(max_df=0.9, max_features=2000,
                                 min_df=0.1, stop_words='english',
                                 use_idf=True, tokenizer=my_tokenizer, ngram_range=(1,2))

tfidf_matrix = tfidf_model.fit_transform(['blah', 'lobe', 'you']) #fit the vectorizer to synopses

print ("In total, there are " + str(tfidf_matrix.shape[0]) + \
      " emails and " + str(tfidf_matrix.shape[1]) + " terms.")
tfidf_model.vocabulary_

In total, there are 3 emails and 2 terms.


{'blah': 0, 'lobe': 1}

{'account': 0,
 'bank': 1,
 'called': 2,
 'company': 3,
 'credit': 4,
 'credit report': 5,
 'day': 6,
 'debt': 7,
 'ha': 8,
 'information': 9,
 'letter': 10,
 'loan': 11,
 'month': 12,
 'paid': 13,
 'pay': 14,
 'payment': 15,
 'received': 16,
 'report': 17,
 'sent': 18,
 'time': 19,
 'told': 20,
 'wa': 21,
 'xx': 22,
 'xx xx': 23,
 'xx xx xxxx': 24,
 'xx xxxx': 25,
 'xxxx xxxx': 26,
 'xxxx xxxx xxxx': 27,
 'year': 28}

In [100]:
from sklearn.decomposition import LatentDirichletAllocation
lda = LatentDirichletAllocation(n_components=5, learning_method = 'online')

In [101]:
tfidf_matrix_lda = (tfidf_matrix * 100)
tfidf_matrix_lda = tfidf_matrix_lda.astype(int)

In [102]:
lda.fit(tfidf_matrix_lda)

LatentDirichletAllocation(batch_size=128, doc_topic_prior=None,
             evaluate_every=-1, learning_decay=0.7,
             learning_method='online', learning_offset=10.0,
             max_doc_update_iter=100, max_iter=10, mean_change_tol=0.001,
             n_components=5, n_jobs=1, n_topics=None, perp_tol=0.1,
             random_state=None, topic_word_prior=None,
             total_samples=1000000.0, verbose=0)

In [105]:
topic_word = lda.components_
print(topic_word.shape)

(5, 29)


In [108]:
import numpy as np
tf_selected_words = tfidf_model.get_feature_names()
n_top_words = 7
topic_keywords_list = []
for i, topic_dist in enumerate(topic_word):
    #Here we select top(n_top_words-1)
    lda_topic_words = np.array(tf_selected_words)[np.argsort(topic_dist)][:-n_top_words:-1] 
    for j in range(len(lda_topic_words)):
        lda_topic_words[j] = vocab_frame_dict[lda_topic_words[j]]
    topic_keywords_list.append(lda_topic_words.tolist())

NameError: name 'vocab_frame_dict' is not defined

In [22]:
# Create Dictionary
#id2word = corpora.Dictionary(data_lemmatized)
id2word = corpora.Dictionary(emails_cleaned)

# Term Document Frequency
corpus = [id2word.doc2bow(email) for email in emails_cleaned]

# View
#print(corpus[:1])
#print(len(corpus[0]))

In [23]:
# Build LDA model
import numpy as np

NUM_TOPICS = 10
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus, 
                     id2word=id2word,
                     num_topics= NUM_TOPICS, 
                     #random_state=100,
                     #update_every=1,
                     #chunksize=100,
                     passes=10
                     #alpha='auto',
                     #per_word_topics=True
                    )

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

...

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/anaconda3/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id

In [24]:
# Print the Keyword in the 10 topics
print(lda_model.print_topics(num_words=10))

[(0, '0.025*"bank" + 0.018*"account" + 0.015*"check" + 0.013*"money" + 0.011*"received" + 0.008*"funds" + 0.008*"would" + 0.008*"wells" + 0.008*"fargo" + 0.007*"sent"'), (1, '0.010*"federal" + 0.008*"act" + 0.007*"bank" + 0.007*"state" + 0.007*"states" + 0.006*"law" + 0.006*"party" + 0.006*"note" + 0.005*"title" + 0.005*"agreement"'), (2, '0.037*"payment" + 0.022*"payments" + 0.015*"would" + 0.015*"loan" + 0.014*"late" + 0.012*"pay" + 0.011*"made" + 0.011*"interest" + 0.011*"paid" + 0.011*"month"'), (3, '0.022*"call" + 0.022*"told" + 0.019*"called" + 0.017*"would" + 0.014*"phone" + 0.014*"back" + 0.014*"said" + 0.013*"get" + 0.012*"asked" + 0.010*"number"'), (4, '0.043*"debt" + 0.025*"company" + 0.016*"never" + 0.014*"collection" + 0.014*"pay" + 0.010*"owe" + 0.010*"bill" + 0.009*"received" + 0.009*"amount" + 0.009*"owed"'), (5, '0.087*"credit" + 0.043*"report" + 0.026*"account" + 0.024*"reporting" + 0.015*"reported" + 0.015*"information" + 0.013*"removed" + 0.012*"bureaus" + 0.012*"co

In [ ]:
# Compute Perplexity
print('Perplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

In [ ]:
from gensim.models import CoherenceModel
# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=emails_cleaned, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('Coherence Score: ', coherence_lda)

In [25]:
import pyLDAvis
import pyLDAvis.gensim  # don't skip this

# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
vis

PreparedData(topic_coordinates=            Freq  cluster  topics         x         y
topic                                                
2      17.593843        1       1 -0.177468 -0.049384
3      14.483476        1       2 -0.196468 -0.079274
0      12.382867        1       3 -0.108386  0.003873
7      10.463459        1       4  0.171833  0.029978
5       9.535179        1       5  0.136931 -0.134663
4       8.360970        1       6 -0.100228 -0.050154
8       8.292346        1       7  0.026383 -0.097514
6       8.286664        1       8 -0.071813  0.142960
9       6.060781        1       9  0.262300 -0.078619
1       4.540423        1      10  0.056917  0.312796, topic_info=     Category          Freq         Term         Total  loglift  logprob
term                                                                    
1     Default  15887.000000       credit  15887.000000  30.0000  30.0000
115   Default  12854.000000      account  12854.000000  29.0000  29.0000
63    Default   7103.000000       report   7103.000000  28.0000  28.0000
133   Default   4056.000000         card   4056.000000  27.0000  27.0000
136   Default   5788.000000         debt   5788.000000  26.0000  26.0000
88    Default   5795.000000         loan   5795.000000  25.0000  25.0000
336   Default   6518.000000      payment   6518.000000  24.0000  24.0000
141   Default   2552.000000     mortgage   2552.000000  23.0000  23.0000
64    Default   3540.000000    reporting   3540.000000  22.0000  22.0000
373   Default   4611.000000         bank   4611.000000  21.0000  21.0000
337   Default   4058.000000     payments   4058.000000  20.0000  20.0000
460   Default   3311.000000         call   3311.000000  19.0000  19.0000
1824  Default   1453.000000      inquiry   1453.000000  18.0000  18.0000
48    Default   6076.000000  information   6076.000000  17.0000  17.0000
18    Default   2902.000000     accounts   2902.000000  16.0000  16.0000
200   Default   2623.000000   collection   2623.000000  15.0000  15.0000
441   Default   4862.000000         told   4862.000000  14.0000  14.0000
46    Default   1212.000000     identity   1212.000000  13.0000  13.0000
417   Default   2015.000000     consumer   2015.000000  12.0000  12.0000
87    Default   2648.000000         late   2648.000000  11.0000  11.0000
69    Default   1069.000000        theft   1069.000000  10.0000  10.0000
306   Default   4253.000000       called   4253.000000   9.0000   9.0000
391   Default   3340.000000          pay   3340.000000   8.0000   8.0000
25    Default   5219.000000      company   5219.000000   7.0000   7.0000
258   Default   2791.000000      balance   2791.000000   6.0000   6.0000
622   Default   2796.000000        phone   2796.000000   5.0000   5.0000
338   Default   1812.000000     reported   1812.000000   4.0000   4.0000
464   Default   1969.000000        check   1969.000000   3.0000   3.0000
1061  Default   1868.000000     interest   1868.000000   2.0000   2.0000
14    Default   1843.000000      removed   1843.000000   1.0000   1.0000
...       ...           ...          ...           ...      ...      ...
1355  Topic10    207.333237        title    367.452087   2.5199  -5.2227
38    Topic10    402.676727      federal    893.505005   2.2951  -4.5589
913   Topic10    239.623489        party    496.537842   2.3636  -5.0780
727   Topic10    268.703949       states    638.726807   2.2263  -4.9635
1395  Topic10    105.171219        notes    171.393860   2.6038  -5.9015
1423  Topic10    129.817505         code    232.582809   2.5090  -5.6909
19    Topic10    302.487701          act    957.992920   1.9394  -4.8450
54    Topic10    218.529831         note    584.335022   2.1086  -5.1701
4860  Topic10     61.696957   contractor     81.766907   2.8105  -6.4348
1669  Topic10    123.911133        trust    262.184326   2.3427  -5.7375
245   Topic10    269.306854        state    972.826538   1.8078  -4.9612
459   Topic10     93.308174   california    167.354630   2.5079  -6.0212
915   Topic10    172.517